In [1]:
import pandas as pd
from IPython.display import display

In [2]:
def merge_df(files):
    merged_df = pd.DataFrame()
    noms = ["MESG1","MESG2","MESG4","MEWB5","MEWB6","MEWB7"]
    i = 0
    for f in files:
        df = pd.read_csv(f, sep='\t')
        nom_colonne = noms[i]
        df = df.rename(columns={
            'length': f'length_{nom_colonne}',
            'eff_length': f'eff_length_{nom_colonne}',
            'est_counts': f'est_counts_{nom_colonne}',
            'tpm': f'tpm_{nom_colonne}'
        })
        if merged_df.empty:
            merged_df = df
        else:
            merged_df = pd.merge(merged_df, df, on='target_id')
        i += 1
    cols = ['target_id'] 
    types = ['length', 'eff_length', 'est_counts', 'tpm']
    for t in types:
        cols.extend([col for col in merged_df.columns if col.startswith(t)])

    merged_df = merged_df[cols]
    new_col = []
    for i, v in enumerate(merged_df['target_id']):
        v = v.split('_')[-3]+'_'+v.split('_')[-2]
        new_col.append(v)
    merged_df['product_accession'] = new_col
    return merged_df

In [3]:
files = [
    "MESG1_RF/abundance.tsv",
    "MESG2_RF/abundance.tsv",
    "MESG4_RF/abundance.tsv",
    "MEWB5_RF/abundance.tsv",
    "MEWB6_RF/abundance.tsv",
    "MEWB7_RF/abundance.tsv"
]

a = merge_df(files)
pd.set_option('display.max_columns', None)
# pd.set_option('display.max_rows', None)
print(len(a))
display(a)

35353


target_id  length_MESG1  length_MESG2  \
0          lcl|NC_004354.4_ncrna_NR_003723.2_1           214           214   
1        lcl|NC_004354.4_mrna_NM_001103384.3_2          1894          1894   
2        lcl|NC_004354.4_mrna_NM_001258513.2_3          2028          2028   
3        lcl|NC_004354.4_mrna_NM_001258512.2_4          2036          2036   
4        lcl|NC_004354.4_mrna_NM_001297796.1_5          5089          5089   
...                                        ...           ...           ...   
35348  lcl|NC_024511.2_trna_Dmel_CR34091_35349            66            66   
35349  lcl|NC_024511.2_trna_Dmel_CR34093_35350            65            65   
35350  lcl|NC_024511.2_rrna_Dmel_CR34094_35351          1324          1324   
35351  lcl|NC_024511.2_trna_Dmel_CR34095_35352            73            73   
35352  lcl|NC_024511.2_rrna_Dmel_CR34096_35353           786           786   

       length_MESG4  length_MEWB5  length_MEWB6  length_MEWB7  \
0               214           214           214           214   
1              1894          1894          1894          1894   
2              2028          2028          2028          2028   
3              2036          2036          2036          2036   
4              5089          5089          5089          5089   
...             ...           ...           ...           ...   
35348            66            66            66            66   
35349            65            65            65            65   
35350          1324          1324          1324          1324   
35351            73            73            73            73   
35352           786           786           786           786   

       eff_length_MESG1  eff_length_MESG2  eff_length_MESG4  eff_length_MEWB5  \
0              97.00000          97.00000          97.00000          97.00000   
1            1777.00000        1777.00000        1777.00000        1777.00000   
2            1911.00000        1911.00000        1911.00000        1911.00000   
3            1919.00000        1919.00000        1919.00000        1919.00000   
4            4972.00000        4972.00000        4972.00000        4972.00000   
...                 ...               ...               ...               ...   
35348           5.79122           5.79122           5.79122           5.79122   
35349           5.71729           5.71729           5.71729           5.71729   
35350        1207.00000        1207.00000        1207.00000        1207.00000   
35351           6.36587           6.36587           6.36587           6.36587   
35352         669.00000         669.00000         669.00000         669.00000   

       eff_length_MEWB6  eff_length_MEWB7  est_counts_MESG1  est_counts_MESG2  \
0              97.00000          97.00000           85.8989           118.368   
1            1777.00000        1777.00000            0.0000             2.000   
2            1911.00000        1911.00000            0.0000             0.000   
3            1919.00000        1919.00000            0.0000             0.000   
4            4972.00000        4972.00000          131.9400           141.575   
...                 ...               ...               ...               ...   
35348           5.79122           5.79122            0.0000             0.000   
35349           5.71729           5.71729            0.0000             0.000   
35350        1207.00000        1207.00000       240513.0000        226787.000   
35351           6.36587           6.36587            0.0000             0.000   
35352         669.00000         669.00000          150.0000           172.000   

       est_counts_MESG4  est_counts_MEWB5  est_counts_MEWB6  est_counts_MEWB7  \
0               54.6776          313.6800        333.661000        247.627000   
1                0.0000          671.9990        224.886000        856.451000   
2                0.0000           56.1272         12.045800          0.025923   
3                0.0000          100.8740        

In [4]:
def moyenne(dataframe, col1, col2, col3):
    if len(col1.split('_')) == 2:
        nom = col1.split('_')[0]+'_'+col1.split('_')[1][2:4]
    else:
        nom = col1.split('_')[0]+'_'+col1.split('_')[1]+'_'+col1.split('_')[2][2:4]
    dataframe[f'{nom}_moyenne'] = dataframe[[col1, col2, col3]].mean(axis=1)
    return dataframe

columns = a.columns
for i in range(1, len(columns) - 2, 3):
    col1, col2, col3 = columns[i], columns[i+1], columns[i+2]
    a = moyenne(a, col1, col2, col3)

display(a)

target_id  length_MESG1  length_MESG2  \
0          lcl|NC_004354.4_ncrna_NR_003723.2_1           214           214   
1        lcl|NC_004354.4_mrna_NM_001103384.3_2          1894          1894   
2        lcl|NC_004354.4_mrna_NM_001258513.2_3          2028          2028   
3        lcl|NC_004354.4_mrna_NM_001258512.2_4          2036          2036   
4        lcl|NC_004354.4_mrna_NM_001297796.1_5          5089          5089   
...                                        ...           ...           ...   
35348  lcl|NC_024511.2_trna_Dmel_CR34091_35349            66            66   
35349  lcl|NC_024511.2_trna_Dmel_CR34093_35350            65            65   
35350  lcl|NC_024511.2_rrna_Dmel_CR34094_35351          1324          1324   
35351  lcl|NC_024511.2_trna_Dmel_CR34095_35352            73            73   
35352  lcl|NC_024511.2_rrna_Dmel_CR34096_35353           786           786   

       length_MESG4  length_MEWB5  length_MEWB6  length_MEWB7  \
0               214           214           214           214   
1              1894          1894          1894          1894   
2              2028          2028          2028          2028   
3              2036          2036          2036          2036   
4              5089          5089          5089          5089   
...             ...           ...           ...           ...   
35348            66            66            66            66   
35349            65            65            65            65   
35350          1324          1324          1324          1324   
35351            73            73            73            73   
35352           786           786           786           786   

       eff_length_MESG1  eff_length_MESG2  eff_length_MESG4  eff_length_MEWB5  \
0              97.00000          97.00000          97.00000          97.00000   
1            1777.00000        1777.00000        1777.00000        1777.00000   
2            1911.00000        1911.00000        1911.00000        1911.00000   
3            1919.00000        1919.00000        1919.00000        1919.00000   
4            4972.00000        4972.00000        4972.00000        4972.00000   
...                 ...               ...               ...               ...   
35348           5.79122           5.79122           5.79122           5.79122   
35349           5.71729           5.71729           5.71729           5.71729   
35350        1207.00000        1207.00000        1207.00000        1207.00000   
35351           6.36587           6.36587           6.36587           6.36587   
35352         669.00000         669.00000         669.00000         669.00000   

       eff_length_MEWB6  eff_length_MEWB7  est_counts_MESG1  est_counts_MESG2  \
0              97.00000          97.00000           85.8989           118.368   
1            1777.00000        1777.00000            0.0000             2.000   
2            1911.00000        1911.00000            0.0000             0.000   
3            1919.00000        1919.00000            0.0000             0.000   
4            4972.00000        4972.00000          131.9400           141.575   
...                 ...               ...               ...               ...   
35348           5.79122           5.79122            0.0000             0.000   
35349           5.71729           5.71729            0.0000             0.000   
35350        1207.00000        1207.00000       240513.0000        226787.000   
35351           6.36587           6.36587            0.0000             0.000   
35352         669.00000         669.00000          150.0000           172.000   

       est_counts_MESG4  est_counts_MEWB5  est_counts_MEWB6  est_counts_MEWB7  \
0               54.6776          313.6800        333.661000        247.627000   
1                0.0000          671.9990        224.886000        856.451000   
2                0.0000           56.1272         12.045800          0.025923   
3                0.0000          100.8740        

In [21]:
tab_corr = pd.read_table('/Users/arthur/PROJECTS/Stage_IJM/data/genomes/melanogaster/GCF_000001215.4_Release_6_plus_ISO1_MT_feature_table.txt')
tab_corr = tab_corr[tab_corr['product_accession'].isin(a['product_accession'])]
tab_corr = tab_corr.reset_index()
valeurs = tab_corr['product_accession'].values
missing_values = []
for i in range(len(a)):
    if a['product_accession'][i] not in tab_corr['product_accession'].values:
        missing_values.append(a['product_accession'][i])
missing_df = pd.DataFrame({'product_accession': missing_values})
tab_corr = pd.concat([tab_corr, missing_df])
tab_corr.to_csv('table_meta.csv', index=False)

In [7]:
pd.reset_option('display.max_columns')
a2 = a
a2 = a2.set_index('target_id')
display(a2)
a2 = a2.transpose()
a2 = a2.reset_index()
display(a2)
a2.to_csv('count_ME_RF.tsv', sep='\t', index=False)

length_MESG1  length_MESG2  \
target_id                                                             
lcl|NC_004354.4_ncrna_NR_003723.2_1               214           214   
lcl|NC_004354.4_mrna_NM_001103384.3_2            1894          1894   
lcl|NC_004354.4_mrna_NM_001258513.2_3            2028          2028   
lcl|NC_004354.4_mrna_NM_001258512.2_4            2036          2036   
lcl|NC_004354.4_mrna_NM_001297796.1_5            5089          5089   
...                                               ...           ...   
lcl|NC_024511.2_trna_Dmel_CR34091_35349            66            66   
lcl|NC_024511.2_trna_Dmel_CR34093_35350            65            65   
lcl|NC_024511.2_rrna_Dmel_CR34094_35351          1324          1324   
lcl|NC_024511.2_trna_Dmel_CR34095_35352            73            73   
lcl|NC_024511.2_rrna_Dmel_CR34096_35353           786           786   

                                         length_MESG4  length_MEWB5  \
target_id                                                             
lcl|NC_004354.4_ncrna_NR_003723.2_1               214           214   
lcl|NC_004354.4_mrna_NM_001103384.3_2            1894          1894   
lcl|NC_004354.4_mrna_NM_001258513.2_3            2028          2028   
lcl|NC_004354.4_mrna_NM_001258512.2_4            2036          2036   
lcl|NC_004354.4_mrna_NM_001297796.1_5            5089          5089   
...                                               ...           ...   
lcl|NC_024511.2_trna_Dmel_CR34091_35349            66            66   
lcl|NC_024511.2_trna_Dmel_CR34093_35350            65            65   
lcl|NC_024511.2_rrna_Dmel_CR34094_35351          1324          1324   
lcl|NC_024511.2_trna_Dmel_CR34095_35352            73            73   
lcl|NC_024511.2_rrna_Dmel_CR34096_35353           786           786   

                                         length_MEWB6  length_MEWB7  \
target_id                                                             
lcl|NC_004354.4_ncrna_NR_003723.2_1               214           214   
lcl|NC_004354.4_mrna_NM_001103384.3_2            1894          1894   
lcl|NC_004354.4_mrna_NM_001258513.2_3            2028          2028   
lcl|NC_004354.4_mrna_NM_001258512.2_4            2036          2036   
lcl|NC_004354.4_mrna_NM_001297796.1_5            5089          5089   
...                                               ...           ...   
lcl|NC_024511.2_trna_Dmel_CR34091_35349            66            66   
lcl|NC_024511.2_trna_Dmel_CR34093_35350            65            65   
lcl|NC_024511.2_rrna_Dmel_CR34094_35351          1324          1324   
lcl|NC_024511.2_trna_Dmel_CR34095_35352            73            73   
lcl|NC_024511.2_rrna_Dmel_CR34096_35353           786           786   

                                         eff_length_MESG1  eff_length_MESG2  \
target_id                                                                     
lcl|NC_004354.4_ncrna_NR_003723.2_1              97.00000          97.00000   
lcl|NC_004354.4_mrna_NM_001103384.3_2          1777.00000        1777.00000   
lcl|NC_004354.4_mrna_NM_001258513.2_3          1911.00000        1911.00000   
lcl|NC_004354.4_mrna_NM_001258512.2_4          1919.00000        1919.00000   
lcl|NC_004354.4_mrna_NM_001297796.1_5          4972.00000        4972.00000   
...                                                   ...               ...   
lcl|NC_024511.2_trna_Dmel_CR34091_35349           5.79122           5.79122   
lcl|NC_024511.2_trna_Dmel_CR34093_35350           5.71729           5.71729   
lcl|NC_024511.2_rrna_Dmel_CR34094_35351        1207.00000        1207.00000   
lcl|NC_024511.2_trna_Dmel_CR34095_35352           6.36587           6.36587   
lcl|NC_024511.2_rrna_Dmel_CR34096_35353         669.00000         669.00000   

                                         eff_length_MESG4  eff_length_MEWB5  \
target_id                                                                     
lcl|NC_004354.4_ncrna_NR_003723.2_1              97.00000          97.00000   
lcl|

target_id                  index lcl|NC_004354.4_ncrna_NR_003723.2_1  \
0                   length_MESG1                                 214   
1                   length_MESG2                                 214   
2                   length_MESG4                                 214   
3                   length_MEWB5                                 214   
4                   length_MEWB6                                 214   
5                   length_MEWB7                                 214   
6               eff_length_MESG1                                97.0   
7               eff_length_MESG2                                97.0   
8               eff_length_MESG4                                97.0   
9               eff_length_MEWB5                                97.0   
10              eff_length_MEWB6                                97.0   
11              eff_length_MEWB7                                97.0   
12              est_counts_MESG1                             85.8989   
13              est_counts_MESG2                             118.368   
14              est_counts_MESG4                             54.6776   
15              est_counts_MEWB5                              313.68   
16              est_counts_MEWB6                             333.661   
17              est_counts_MEWB7                             247.627   
18                     tpm_MESG1                             53.2475   
19                     tpm_MESG2                             46.6189   
20                     tpm_MESG4                             33.0387   
21                     tpm_MEWB5                             454.102   
22                     tpm_MEWB6                             399.273   
23                     tpm_MEWB7                             299.026   
24             product_accession                         NR_003723.2   
25             length_SG_moyenne                               214.0   
26             length_WB_moyenne                               214.0   
27         eff_length_SG_moyenne                                97.0   
28         eff_length_WB_moyenne                                97.0   
29         est_counts_SG_moyenne                           86.314833   
30         est_counts_WB_moyenne                          298.322667   
31                tpm_SG_moyenne                             44.3017   
32                tpm_WB_moyenne                          384.133667   

target_id lcl|NC_004354.4_mrna_NM_001103384.3_2  \
0                                          1894   
1                                          1894   
2                                          1894   
3                                          1894   
4                                          1894   
5                                          1894   
6                                        1777.0   
7                                        1777.0   
8                                        1777.0   
9                                        1777.0   
10                                       1777.0   
11                                       1777.0   
12                                          0.0   
13                                          2.0   
14                                          0.0   
15                                      671.999   
16                                      224.886   
17                                      856.451   
18                                          0.0   
19                                     0.042997   
20                                          0.0   
21                                       53.103   
22                                      14.6896   
23                                      56.4543   
24                               NM_001103384.3   
25                                       1894.0   
26                                       1894.0   
27                                       1777.0   
28                                       1777.0   
29                   

In [5]:
tab_cor = pd.read_table('/Users/arthur/PROJECTS/Stage_IJM/data/genomes/melanogaster/GCF_000001215.4_Release_6_plus_ISO1_MT_feature_table.txt')
new_df = pd.merge(a, tab_cor, how='left', on='product_accession')
new_df = new_df.sort_values(by='tpm_SG_moyenne', ascending=False)
new_df = new_df.reset_index()
new_df = new_df.drop(columns=['index'])
new_df = new_df.reset_index()
new_df.to_csv("merged_abundance_ME_RF.csv", index=False)
pd.set_option('display.max_columns', None)
display(new_df.head(40))

index                                   target_id  length_MESG1  \
0       0      lcl|NT_037436.4_mrna_NM_057370.2_23336           321   
1       1      lcl|NT_037436.4_mrna_NM_079300.3_23338          1109   
2       2      lcl|NT_037436.4_mrna_NM_057371.3_23335           359   
3       3        lcl|NC_004354.4_mrna_NM_057369.4_932           952   
4       4      lcl|NT_033777.3_mrna_NM_079664.2_30721           636   
5       5   lcl|NT_033777.3_mrna_NM_001170166.1_30723           327   
6       6      lcl|NT_033777.3_mrna_NM_169764.3_30720           550   
7       7      lcl|NT_037436.4_mrna_NM_140480.3_24230           544   
8       8      lcl|NT_037436.4_mrna_NM_079368.3_24397          1486   
9       9       lcl|NT_033779.5_mrna_NM_134912.3_7107           406   
10     10       lcl|NT_033779.5_mrna_NM_164529.3_7105           491   
11     11      lcl|NT_033777.3_mrna_NM_142116.2_29831           587   
12     12      lcl|NT_037436.4_mrna_NM_140484.3_24238           677   
13     13   lcl|NW_007931121.1_rrna_NR_133555.1_35319          1995   
14     14     lcl|NC_024511.2_rrna_Dmel_CR34094_35351          1324   
15     15      lcl|NT_033778.4_mrna_NM_137981.2_19288           581   
16     16      lcl|NT_037436.4_mrna_NM_168767.2_25205           470   
17     17   lcl|NW_007931121.1_rrna_NR_133562.1_35329          3970   
18     18    lcl|NT_033779.5_mrna_NM_001169386.2_7156           411   
19     19      lcl|NT_033777.3_mrna_NM_169585.2_29830           483   
20     20       lcl|NT_033779.5_mrna_NM_078751.4_7576          3950   
21     21      lcl|NT_033778.4_mrna_NM_058027.5_15129          2029   
22     22      lcl|NT_033778.4_mrna_NM_137979.3_19285           659   
23     23   lcl|NT_033778.4_mrna_NM_001014551.3_19777           320   
24     24      lcl|NT_033779.5_mrna_NM_135695.2_10042           776   
25     25        lcl|NC_004354.4_mrna_NM_130694.3_926           557   
26     26    lcl|NT_033779.5_mrna_NM_001298648.1_7106           468   
27     27   lcl|NT_033777.3_mrna_NM_001300371.1_29214           700   
28     28      lcl|NT_033777.3_mrna_NM_142114.3_29828           587   
29     29   lcl|NT_033777.3_mrna_NM_001202313.1_30680           500   
30     30   lcl|NT_033777.3_mrna_NM_001104349.2_30674           688   
31     31       lcl|NC_004354.4_mrna_NM_134609.2_5861           643   
32     32   lcl|NT_037436.4_mrna_NM_001274927.2_24232           375   
33     33      lcl|NT_033777.3_mrna_NM_141689.3_28493           502   
34     34      lcl|NT_037436.4_mrna_NM_140419.3_24016           565   
35     35       lcl|NT_033779.5_mrna_NM_057282.4_6291           601   
36     36  lcl|NW_007931121.1_rrna_Dmel_CR45851_35309          1721   
37     37      lcl|NT_037436.4_mrna_NM_080275.3_23244           568   
38     38   lcl|NT_037436.4_mrna_NM_001274926.2_24231           516   
39     39      lcl|NT_037436.4_mrna_NM_080077.2_23572          2304   

    length_MESG2  length_MESG4  length_MEWB5  length_MEWB6  length_MEWB7  \
0            321           321           321           321           321   
1           1109          1109          1109          1109          1109   
2            359           359           359           359           359   
3            952           952           952           952           952   
4            636           636           636           636           636   
5            327           327           327           327           327   
6            550           550           550           550           550   
7            544           544           544           544           544   
8           1486          1486          1486          1486          1486   
9            406           406           406           406           406   
10           491           491           491           491           491   
11           587           587           587           587           587   
12           677           677           677           677           677   
13          1995          19

In [12]:
res_sleuth = pd.read_csv('sleuth_results_ME_RF.csv')

new_col = []
for i, v in enumerate(res_sleuth['target_id']):
    v = v.split('_')[-3]+'_'+v.split('_')[-2]
    new_col.append(v)
res_sleuth['product_accession'] = new_col

tab_cor = pd.read_table('/Users/arthur/PROJECTS/Stage_IJM/data/genomes/melanogaster/GCF_000001215.4_Release_6_plus_ISO1_MT_feature_table.txt')
res_sleuth = pd.merge(res_sleuth, tab_cor, how='left', on='product_accession')
res_sleuth.to_csv('sleuth_results_trie_ME_RF.csv')
display(res_sleuth.head(10))
index = res_sleuth[res_sleuth['symbol'] == 'Eig71Ee'].index
print(index)

target_id           pval           qval  \
0     lcl|NT_033777.3_mrna_NM_079830.4_34286   0.000000e+00   0.000000e+00   
1     lcl|NT_033777.3_mrna_NM_169182.2_27709   0.000000e+00   0.000000e+00   
2     lcl|NT_033778.4_mrna_NM_057273.4_13918   0.000000e+00   0.000000e+00   
3  lcl|NT_033777.3_mrna_NM_001275633.1_29734  3.305172e-270  1.506745e-266   
4     lcl|NT_033778.4_mrna_NM_078970.4_15010  2.992215e-256  1.091261e-252   
5     lcl|NT_037436.4_mrna_NM_079220.2_21712  2.119157e-253  6.440470e-250   
6      lcl|NC_004354.4_mrna_NM_132983.3_4788  3.498568e-250  9.113771e-247   
7     lcl|NT_033778.4_mrna_NM_136526.2_13883  7.833472e-243  1.785542e-239   
8     lcl|NT_037436.4_mrna_NM_139756.3_21716  6.365772e-239  1.289776e-235   
9  lcl|NT_033777.3_mrna_NM_001300669.1_34284  5.935906e-235  1.082412e-231   

           b      se_b  mean_obs    var_obs  tech_var  sigma_sq  \
0 -10.229093  0.244448  4.421399  31.398745  0.000053  0.010500   
1   3.893563  0.099916  7.624523   4.557184  0.001541  0.010001   
2 -10.871797  0.282519  4.742751  35.554571  0.000018  0.119708   
3  -9.871007  0.281063  4.242356  29.285838  0.000136  0.068368   
4 -10.554266  0.308660  4.583986  33.532083  0.000020  0.142887   
5  -9.810342  0.288527  4.212024  28.941105  0.000039  0.085290   
6  -9.798751  0.290049  4.206228  28.875181  0.000043  0.088110   
7   3.443112  0.103463  6.968585   3.562530  0.002361  0.005168   
8 -10.193626  0.308829  4.403666  31.287456  0.000035  0.143027   
9  -9.743364  0.297693  4.178535  28.504584  0.000122  0.030682   

   smooth_sigma_sq  final_sigma_sq product_accession # feature class  \
0         0.089579        0.089579       NM_079830.4      mRNA   NaN   
1         0.013434        0.013434       NM_169182.2      mRNA   NaN   
2         0.053962        0.119708       NM_057273.4      mRNA   NaN   
3         0.118359        0.118359    NM_001275633.1      mRNA   NaN   
4         0.069274        0.142887       NM_078970.4      mRNA   NaN   
5         0.124832        0.124832       NM_079220.2      mRNA   NaN   
6         0.126150        0.126150       NM_132983.3      mRNA   NaN   
7         0.013696        0.013696       NM_136526.2      mRNA   NaN   
8         0.092091        0.143027       NM_139756.3      mRNA   NaN   
9         0.132810        0.132810    NM_001300669.1      mRNA   NaN   

          assembly     assembly_unit    seq_type chromosome genomic_accession  \
0  GCF_000001215.4  Primary Assembly  chromosome         3R       NT_033777.3   
1  GCF_000001215.4  Primary Assembly  chromosome         3R       NT_033777.3   
2  GCF_000001215.4  Primary Assembly  chromosome         2R       NT_033778.4   
3  GCF_000001215.4  Primary Assembly  chromosome         3R       NT_033777.3   
4  GCF_000001215.4  Primary Assembly  chromosome         2R       NT_033778.4   
5  GCF_000001215.4  Primary Assembly  chromosome         3L       NT_037436.4   
6  GCF_000001215.4  Primary Assembly  chromosome          X       NC_004354.4   
7  GCF_000001215.4  Primary Assembly  chromosome         2R       NT_033778.4   
8  GCF_000001215.4  Primary Assembly  chromosome         3L       NT_037436.4   
9  GCF_000001215.4  Primary Assembly  chromosome         3R       NT_033777.3   

        start         end strand  non-redundant_refseq related_accession  \
0  29923754.0  29924615.0      -                   NaN       NP_524554.1   
1   7345069.0   7346354.0      +                   NaN       NP_731155.2   
2   8435443.0   8436011.0      +                   NaN       NP_476621.1   
3  14152211.0  14152650.0      -                   NaN    NP_001262562.1   
4  11355319.0  11356128.0      +                   NaN       NP_523694.2   
5   6035216.0   6036175.0      +                   NaN       NP_523944.1   
6  17281777.0  17282726.0      -                   NaN       NP_573211.1   
7   8267643.0   8269334.0      -                   NaN       NP_610370.1   
8   6050757.0   6051690.0      +                   NaN       NP_64801

Index([267], dtype='int64')


In [6]:
from Bio import Entrez, SeqIO, Seq

def get_gene_info(gene):
    Entrez.email = "akdgljs@gmail.com"
    stream = Entrez.efetch(db="nucleotide", id=gene, retmode="text", rettype="gb")
    record = SeqIO.read(stream, "genbank")
    stream.close()
    
    gene_info = {
        "Gene ID": gene,
        "Nom": "",
        "Length": len(record),
        "Definition": record.description,
        "Organism": record.annotations.get("organism", "Unknown"),
        "Protein Translation": "",
        "Signal Peptide": "Not Available",
        "pT": 0,
        "pP": 0,
        "pS": 0,
        "pC": 0
    }
    
    for feature in record.features:
        if feature.type == "CDS":
            gene_info["Protein Translation"] = feature.qualifiers.get("translation", [""])[0]
            gene_info["Nom"] = feature.qualifiers.get("gene", [""])[0]
            # Check for signal peptide feature
            if "signal_peptide" in feature.qualifiers:
                gene_info["Signal Peptide"] = feature.qualifiers["signal_peptide"][0]

    seq = gene_info["Protein Translation"]
    if seq.find("T") != -1:
        gene_info["pT"] = 100*seq.count("T")/len(seq)
    else:
        gene_info["pT"] = 0
    if seq.find("P") != -1:
        gene_info["pP"] = 100*seq.count("P")/len(seq)
    else:
        gene_info["pP"] = 0
    if seq.find("S") != -1:
        gene_info["pS"] = 100*seq.count("S")/len(seq)
    else:
        gene_info["pS"] = 0
    if seq.find("C") != -1:
        gene_info["pC"] = 100*seq.count("C")/len(seq)
    else:
        gene_info["pC"] = 0
    
    return gene_info

gene = 'NM_001170166.1'
get_gene_info(gene)

{'Gene ID': 'NM_001170166.1',
 'Nom': 'CG7606',
 'Length': 327,
 'Definition': 'Drosophila melanogaster uncharacterized protein, transcript variant B (CG7606), mRNA',
 'Organism': 'Drosophila melanogaster',
 'Protein Translation': 'MFNIKLIILVALTISMVQSCSVEEPEQVECGCGCGKPQCLSCGSRSCGCGCNPCRCPSSSGCGCKD',
 'Signal Peptide': 'Not Available',
 'pT': 1.5151515151515151,
 'pP': 6.0606060606060606,
 'pS': 13.636363636363637,
 'pC': 19.696969696969695}

In [7]:
def get_signal(gene):
    g1 = gene.split('.')[0]
    g2 = gene.split('.')[1]
    df = pd.read_table(f'res_signalp_RF/output_{g1}_{g2}_plot.txt',header = 1)
    sig = ""
    for l in df['label']:
        if l != "O":
            sig+=l
        else:
            break
    return sig, len(sig)

gene = 'NM_057370.2'
get_signal(gene)

('NNHHHHHHHHHHHHHHHCCCCCC', 23)

In [8]:
df_final = pd.DataFrame()
for gene_id in new_df.head(50)['product_accession']:
    if gene_id.startswith('Dmel'):
        new_row ={
            "Gene ID": gene_id,
            "Nom": "None",
            "Definition": "None",
            "TPM SG moyen": new_df[new_df['product_accession'] == gene_id]['tpm_SG_moyenne'].values[0],
            "TPM WB moyen": new_df[new_df['product_accession'] == gene_id]['tpm_WB_moyenne'].values[0],
            "Taille": "None",
            "% Threonine": "None",
            "% Proline": "None",
            "% Serine": "None",
            "% Cysteine": "None",
            "Sequence": "None",
            "Peptide Signal": "None"
        }
    else:
        gene_info = get_gene_info(gene_id)
        sig, taille = "None", "None"
        if gene_id.startswith('NM'):
            sig, taille = get_signal(gene_id)
        new_row = {
            "Gene ID": gene_info["Gene ID"],
            "Nom": gene_info["Nom"],
            "Definition": gene_info["Definition"],
            "TPM SG moyen": new_df[new_df['product_accession'] == gene_id]['tpm_SG_moyenne'].values[0],
            "TPM WB moyen": new_df[new_df['product_accession'] == gene_id]['tpm_WB_moyenne'].values[0],
            "Taille": len(gene_info["Protein Translation"]),
            "% Threonine": gene_info["pT"],
            "% Proline": gene_info["pP"],
            "% Serine": gene_info["pS"],
            "% Cysteine": gene_info["pC"],
            "Sequence": gene_info["Protein Translation"],
            "Peptide Signal": (sig, taille)
        }
    df_final = pd.concat([df_final, pd.DataFrame([new_row])], ignore_index=True)

df_final.to_csv('final_table_RF.csv', index=False)
display(df_final)

Gene ID         Nom  \
0      NM_057370.2        Sgs7   
1      NM_079300.3        Sgs3   
2      NM_057371.3        Sgs8   
3      NM_057369.4        Sgs4   
4      NM_079664.2        Sgs5   
5   NM_001170166.1      CG7606   
6      NM_169764.3     Sgs5bis   
7      NM_140480.3     CG12310   
8      NM_079368.3     Eig71Ee   
9      NM_134912.3     CG15404   
10     NM_164529.3     CG31698   
11     NM_142116.2     CG14852   
12     NM_140484.3     CG13460   
13     NR_133555.1               
14    Dmel_CR34094        None   
15     NM_137981.2     CG11300   
16     NM_168767.2     CG32198   
17     NR_133562.1               
18  NM_001169386.2     CG42460   
19     NM_169585.2      CG8087   
20     NM_078751.4        Sgs1   
21     NM_058027.5  eEF1alpha1   
22     NM_137979.3     CG13560   
23  NM_001014551.3       RpL41   
24     NM_135695.2      CG6770   
25     NM_130694.3     CG14265   
26  NM_001298648.1     CG15404   
27  NM_001300371.1        Sgsf   
28     NM_142114.3         Jig   
29  NM_001202313.1     CG42798   
30  NM_001104349.2     CG34279   
31     NM_134609.2     CG10918   
32  NM_001274927.2     CG43679   
33     NM_141689.3       RpS29   
34     NM_140419.3     CG17362   
35     NM_057282.4       RpLP1   
36    Dmel_CR45851        None   
37     NM_080275.3         nol   
38  NM_001274926.2     CG43679   
39     NM_080077.2        Lsp2   
40     NM_080321.1         ng3   
41     NM_079879.4       RpS3A   
42     NM_057329.4        Pig1   
43     NM_057966.5       RpL39   
44     NR_037753.2               
45     NR_001992.2               
46  NM_001299481.1       RpS23   
47  NM_001272632.2     RpL37-1   
48     NM_137292.4       RpS15   
49     NM_166383.4       RpS18   

                                           Definition   TPM SG moyen  \
0   Drosophila melanogaster salivary gland secreti...  259046.333333   
1   Drosophila melanogaster salivary gland secreti...  158939.000000   
2   Drosophila melanogaster salivary gland secreti...   63435.066667   
3   Drosophila melanogaster salivary gland secreti...   53900.766667   
4   Drosophila melanogaster salivary gland secreti...   46692.900000   
5   Drosophila melanogaster uncharacterized protei...   42454.866667   
6     Drosophila melanogaster Sgs5bis (Sgs5bis), mRNA   29669.166667   
7   Drosophila melanogaster uncharacterized protei...   25164.766667   
8   Drosophila melanogaster Ecdysone-induced gene ...   21543.000000   
9   Drosophila melanogaster uncharacterized protei...   18237.133333   
10  Drosophila melanogaster uncharacterized protei...   17962.933333   
11  Drosophila melanogaster uncharacterized protei...   12235.700000   
12  Drosophila melanogaster uncharacterized protei...   11862.650000   
13  Drosophila melanogaster 18S ribosomal RNA (18S...   10155.466667   
14                                               None    8986.583333   
15  Drosophila melanogaster uncharacterized protei...    5387.010000   
16  Drosophila melanogaster uncharacterized protei...    4921.940000   
17  Drosophila melanogaster 28S ribosomal RNA (28S...    4861.533333   
18  Drosophila melanogaster uncharacterized protei...    4515.520000   
19  Drosophila melanogaster uncharacterized protei...    3113.860000   
20  Drosophila melanogaster salivary gland secreti...    3057.726667   
21  Drosophila melanogaster eukaryotic translation...    2967.360000   
22  Drosophila melanogaster uncharacterized protei...    2855.899000   
23  Drosophila melanogaster ribosomal protein L41 ...    2835.206667   
24  Drosophila melanogaster uncharacterized protei...    2736.716667   
25  Drosophila melanogaster uncharacterized protei...    2322.400000   
26  Drosophila melanogaster uncharacterized protei...    2145.663333   
27  Drosophila melanogaster salivary gland-derived...    2142.906667   
28            Drosophila melanogaster Jig (Jig), mRNA    2020.475333   
29  Drosophila melanogaster uncharacterized protei...    1816.681000   
30  Drosophila melanogaster uncharacterized 

In [36]:
with open('prot50_FR.fasta','a') as f:
    for gene_id in new_df.head(50)['product_accession']:
        if gene_id.startswith('Dmel'):
            continue
        gene_info = get_gene_info(gene_id)
        f.write(f'>{gene_info["Gene ID"]}\n{gene_info["Protein Translation"]}\n')